In [ ]:
!git clone https://github.com/msu-video-group/memfof.git
%cd memfof
!pip3 install -r requirements.txt

In [ ]:
import torch
from core.memfof import MEMFOF
from demo import process_video, AVAILABLE_MODELS

device = "cuda" if torch.cuda.is_available() else "cpu"

print(f"Using {device} for inference")
print("List of available models:")
for model_name in AVAILABLE_MODELS:
    print("\t", model_name)

In [ ]:
model = MEMFOF.from_pretrained("egorchistov/optical-flow-MEMFOF-Tartan-T-TSKH").eval().to(device)

In [ ]:
with torch.inference_mode():
    example_input = torch.randint(0, 256, [1, 3, 3, 1080, 1920], device=device)  # [B=1, T=3, C=3, H=1080, W=1920]
    backward_flow, forward_flow = model(example_input)["flow"][-1].unbind(dim=1)  # [B=1, C=2, H=1080, W=1920]

    max_memory_allocated = torch.cuda.max_memory_allocated()
    print(f"Max allocated memory: {max_memory_allocated / 1024**2:.2f} MB")

In [ ]:
!mkdir -p assets
!wget -O assets/davis_input.mp4 "https://msu-video-group.github.io/memfof/static/videos/davis_input.mp4"

In [ ]:
process_video(model, "assets/davis_input.mp4", "assets/davis_flow.mp4", device)